In [1]:
# <!-- collapse=True -->
import bokeh, bokeh.models
from bokeh.plotting import figure,show,output_file
from bokeh.io import output_notebook
output_notebook()

import geopandas as gpd
from shapely.geometry import Point
import urllib
import dask.dataframe as dd
import dask.distributed
import numpy as np

import sklearn.preprocessing

client = dask.distributed.Client()

coord_system = {'init': 'epsg:4326'}
df = gpd.read_file('./taxi_zones/taxi_zones_new.shp').to_crs(coord_system)
df = df.drop(['Shape_Area', 'Shape_Leng', 'OBJECTID'], axis=1)
df.head()

Loading BokehJS ...

LocationID        borough  \
0           1            EWR   
1           2         Queens   
2           3          Bronx   
3           4      Manhattan   
4           5  Staten Island   

                                            geometry                     zone  
0  POLYGON ((-74.18445299999998 40.6949959999999,...           Newark Airport  
1  (POLYGON ((-73.82337597260664 40.6389870471767...              Jamaica Bay  
2  POLYGON ((-73.84792614099986 40.87134223399993...  Allerton/Pelham Gardens  
3  POLYGON ((-73.9717741096532 40.72582128133706,...            Alphabet City  
4  POLYGON ((-74.17421738099991 40.56256808599989...            Arden Heights

In [2]:
# <!-- collapse=True -->
gjds = bokeh.models.GeoJSONDataSource(geojson=df.to_json())
TOOLS = "pan,wheel_zoom,reset,hover,save"

p = figure(title="NYC Taxi Districts", tools=TOOLS,
    x_axis_location=None, y_axis_location=None, 
    responsive=True)

color_mapper = bokeh.models.LinearColorMapper(palette=bokeh.palettes.Viridis256)

p.patches('xs', 'ys', 
          fill_color={'field': 'LocationID', 'transform': color_mapper},
          fill_alpha=1., line_color="black", line_width=0.5,          
          source=gjds)

p.grid.grid_line_color = None

hover = p.select_one(bokeh.models.HoverTool)
hover.point_policy = "follow_mouse"
hover.tooltips = u"""
<div> 
    <div class="bokeh_hover_tooltip">Name : @zone</div>
    <div class="bokeh_hover_tooltip">Borough : @borough</div>
    <div class="bokeh_hover_tooltip">Zone ID : @LocationID</div>
    <div class="bokeh_hover_tooltip">(Lon, Lat) : ($x ˚E, $y ˚N)</div>
</div>
"""

#p.circle([-73.966,], [40.78,], size=10, fill_color='magenta', line_color='yellow', line_width=1, alpha=1.0)

show(p)

In [3]:
# <!-- collapse=True -->
df2 = df.copy()
df2['geometry'] = df.geometry.envelope
df2['borough_categ'] = sklearn.preprocessing.LabelEncoder().fit_transform(df2['borough'])
gjds2 = bokeh.models.GeoJSONDataSource(geojson=df2.to_json())

TOOLS = "pan,wheel_zoom,reset,hover,save"

p = figure(title="NYC Taxi Districts Bounding Boxes", tools=TOOLS,
    x_axis_location=None, y_axis_location=None, 
    responsive=True)

color_mapper = bokeh.models.LinearColorMapper(palette=bokeh.palettes.Viridis256)

p.patches('xs', 'ys', 
          fill_color={'field': 'borough_categ', 'transform': color_mapper},
          fill_alpha=0.7, line_color="black", line_width=0.5,          
          source=gjds2)

p.grid.grid_line_color = None

hover = p.select_one(bokeh.models.HoverTool)
hover.point_policy = "follow_mouse"
hover.tooltips = u"""
<div> 
    <div class="bokeh_hover_tooltip">Name : @zone</div>
    <div class="bokeh_hover_tooltip">Borough : @borough</div>
    <div class="bokeh_hover_tooltip">Zone ID : @LocationID</div>
    <div class="bokeh_hover_tooltip">(Lon, Lat) : ($x ˚E, $y ˚N)</div>
</div>
"""

#p.circle([-73.966,], [40.78,], size=10, fill_color='magenta', line_color='yellow', line_width=1, alpha=1.0)

show(p)

In [41]:
N = 4000
x = np.random.random(size=N) * 100
y = np.random.random(size=N) * 100
radii = np.random.random(size=N) * 1.5
colors = [
    "#%02x%02x%02x" % (int(r), int(g), 150) for r, g in zip(50+2*x, 30+2*y)
]

TOOLS="hover,crosshair,pan,wheel_zoom,zoom_in,zoom_out,box_zoom,undo,redo,reset,tap,save,box_select,poly_select,lasso_select,"

p = figure(tools=TOOLS)

p.scatter(x, y, radius=radii,
          fill_color=colors, fill_alpha=0.6,
          line_color=None)

#output_file("color_scatter.html", title="color_scatter.py example")

show(p)  # open a browser

In [42]:
import pandas as pd
df=pd.read_csv("./wait_time/august_wait_time.csv")

/home/kun/anaconda2/lib/python2.7/site-packages/IPython/core/interactiveshell.py:2717: DtypeWarning: Columns (3,4,5,6,7,8,10,11,12) have mixed types. Specify dtype option on import or set low_memory=False.
  interactivity=interactivity, compiler=compiler, result=result)


In [43]:
df.head()

Unnamed: 0      pickup_datetime     dropoff_datetime pickup_LocationID  \
0         0.0  2013-08-05 18:04:00  2013-08-05 18:17:00               107   
1         1.0  2013-08-05 20:58:00  2013-08-05 21:09:00                79   
2         2.0  2013-08-05 21:20:00  2013-08-05 21:24:00               161   
3         3.0  2013-08-06 11:02:00  2013-08-06 11:12:00               161   
4         4.0  2013-08-06 11:34:00  2013-08-06 11:44:00               140   

  pickup_long pickup_lat dropoff_LocationID dropoff_long dropoff_lat  \
0    -73.9783    40.7372                237     -73.9648     40.7675   
1    -73.9889    40.7308                236     -73.9546     40.7782   
2    -73.9763    40.7557                237     -73.9686     40.7675   
3    -73.9727    40.7613                236     -73.9542     40.7842   
4    -73.9564    40.7669                237     -73.9665     40.7623   

                          medallion wait_time delta_long delta_lat  
0  3418135604CD3F357DD9577AF978C5C0         3  -0.004524 -0.003593  
1  3418135604CD3F357DD9577AF978C5C0        11  -0.021759 -0.022457  
2  3418135604CD3F357DD9577AF978C5C0         4  -0.001808  -0.00475  
3  3418135604CD3F357DD9577AF978C5C0         4  -0.001182 -0.004468  
4  3418135604CD3F357DD9577AF978C5C0         4  -0.002128  0.000698

In [49]:
from bokeh.plotting import figure, ColumnDataSource
from bokeh.models import HoverTool


def scatter_with_hover(df, x, y,
                       fig=None, cols=None, name=None, marker='x',
                       fig_width=500, fig_height=500, **kwargs):
    """
    Plots an interactive scatter plot of `x` vs `y` using bokeh, with automatic
    tooltips showing columns from `df`.

    Parameters
    ----------
    df : pandas.DataFrame
        DataFrame containing the data to be plotted
    x : str
        Name of the column to use for the x-axis values
    y : str
        Name of the column to use for the y-axis values
    fig : bokeh.plotting.Figure, optional
        Figure on which to plot (if not given then a new figure will be created)
    cols : list of str
        Columns to show in the hover tooltip (default is to show all)
    name : str
        Bokeh series name to give to the scattered data
    marker : str
        Name of marker to use for scatter plot
    **kwargs
        Any further arguments to be passed to fig.scatter

    Returns
    -------
    bokeh.plotting.Figure
        Figure (the same as given, or the newly created figure)

    Example
    -------
    fig = scatter_with_hover(df, 'A', 'B')
    show(fig)

    fig = scatter_with_hover(df, 'A', 'B', cols=['C', 'D', 'E'], marker='x', color='red')
    show(fig)

    Author
    ------
    Robin Wilson <robin@rtwilson.com>
    with thanks to Max Albert for original code example
    """

    # If we haven't been given a Figure obj then create it with default
    # size etc.
    if fig is None:
        fig = figure(width=fig_width, height=fig_height, tools=['box_zoom', 'reset'])

    # We're getting data from the given dataframe
    source = ColumnDataSource(data=df)

    # We need a name so that we can restrict hover tools to just this
    # particular 'series' on the plot. You can specify it (in case it
    # needs to be something specific for other reasons), otherwise
    # we just use 'main'
    if name is None:
        name = 'main'

    # Actually do the scatter plot - the easy bit
    # (other keyword arguments will be passed to this function)
    fig.scatter(df[x], df[y], source=source, name=name, marker=marker, **kwargs)

    # Now we create the hover tool, and make sure it is only active with
    # the series we plotted in the previous line
    hover = HoverTool(names=[name])

    if cols is None:
        # Display *all* columns in the tooltips
        hover.tooltips = [(c, '@' + c) for c in df.columns]
    else:
        # Display just the given columns in the tooltips
        hover.tooltips = [(c, '@' + c) for c in cols]

    hover.tooltips.append(('index', '$index'))

    # Finally add/enable the tool
    fig.add_tools(hover)

    return fig

In [48]:
from bokeh.charts import HeatMap
colors = [
    "#%02x%02x%02x" % (int(r), int(g), 150) for r, g in zip(50+2*x, 30+2*y)
]

TOOLS="hover,crosshair,pan,wheel_zoom,zoom_in,zoom_out,box_zoom,undo,redo,reset,tap,save,box_select,poly_select,lasso_select,"

p = figure(tools=TOOLS)

p.scatter(x, y, radius=radii,
          fill_color=colors, fill_alpha=0.6,
          line_color=None)

p=HeatMap(df[:1000], x='dropoff_long', y='dropoff_lat', title="Dropoff location heatmap",
            xlabel="Dropoff longutide", ylabel="Dropoff lattitude")
#output_file("color_scatter.html", title="color_scatter.py example")

show(p)  # open a browser

ValueError: expected an element of either List(String) or List(Int), got [-73.96480600000001, -73.95459, -73.96862, -73.954239, -73.966454, -73.966766, -73.955872, -73.96390500000001, -73.963539, -73.956886, -73.967972, -73.95636, -73.965408, -73.963531, -73.963722, -73.955269, -73.958878, -73.963791, -73.955566, -73.955048, -73.96462199999999, -73.96350100000001, -73.96157099999999, -73.965034, -73.861305, -73.918152, -73.922501, -73.922882, -73.887199, -73.966171, -73.959694, -73.967361, -73.950188, -73.960838, -73.966698, -73.965523, -73.964325, -73.925613, -73.871193, -73.96508, -73.912598, -73.86541700000001, -73.96129599999999, -73.971214, -73.92313399999999, -73.95037099999999, -73.958549, -73.967735, -73.928635, -73.872559, -73.963661, -73.953239, -73.957001, -73.962715, -73.956367, -73.95839699999999, -73.972603, -73.87258100000001, -73.953484, -73.962936, -73.86206800000001, -73.964417, -73.96755999999999, -73.972031, -73.967628, -73.961052, -73.962418, -73.96687299999999, -7